In [180]:
import pandas as pd
import numpy as np
import random
import folium
import matplotlib.pyplot as plt
import matplotlib.colors as mcolors
from sklearn.cluster import DBSCAN, KMeans

pd.set_option('display.max_columns', None)

In [181]:
df = pd.read_csv('./Traffic_Accidents_2024.csv')

In [182]:
df.head()

X             Y  OBJECTID INCIDENTID           ACCIDENT_DATE  \
0 -1.580702e+07  4.523771e+06         1  23C013957  2024/02/29 23:18:00+00   
1 -1.580511e+07  4.521643e+06         2  24C000041  2024/01/01 00:20:00+00   
2 -1.580513e+07  4.521632e+06         3  24C000041  2024/01/01 00:20:00+00   
3 -1.580504e+07  4.523029e+06         4  24C000084  2024/01/01 01:46:00+00   
4 -1.580542e+07  4.521992e+06         5  24C000127  2024/01/01 03:41:00+00   

               INTERSECTION            LOCATION CROSS_STREET     CITY STATE  \
0  W 21ST ST N & N WACO AVE         W 21ST ST N   N WACO AVE  WICHITA    KS   
1         1145 E LINCOLN ST   1145 E LINCOLN ST          NaN  WICHITA    KS   
2  E LINCOLN ST & S IDA AVE        E LINCOLN ST    S IDA AVE  WICHITA    KS   
3        2330 E CENTRAL AVE  2330 E CENTRAL AVE          NaN  WICHITA    KS   
4           951 E DEWEY AVE     951 E DEWEY AVE          NaN  WICHITA    KS   

   POSTAL_CODE  OFFENSE_CO                                OFFENSE_DE  \
0      67203.0        7090                MOTOR VEHICLE/FIXED OBJECT   
1      67211.0        7030  MOTOR VEHICLE/MOTOR VEHICLE IN TRANSPORT   
2      67211.0        7030  MOTOR VEHICLE/MOTOR VEHICLE IN TRANSPORT   
3      67214.0        6105         PRIVATE PROPERTY/NON-INJURY CRASH   
4      67202.0        6105         PRIVATE PROPERTY/NON-INJURY CRASH   

    LONGITUDE   LATITUDE  YEAR_  MONTH_  DOW_ MONTHFULL   DOWFULL  QUARTER  
0 -141.996855  37.604971   2024       2     4  February  Thursday        1  
1 -141.979709  37.589825   2024       1     1   January    Monday        1  
2 -141.979907  37.589743   2024       1     1   January    Monday        1  
3 -141.979034  37.599688   2024       1     1   January    Monday        1  
4 -141.982486  37.592306   2024       1     1   January    Monday        1

In [183]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20814 entries, 0 to 20813
Data columns (total 21 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   X              20750 non-null  float64
 1   Y              20750 non-null  float64
 2   OBJECTID       20814 non-null  int64  
 3   INCIDENTID     20814 non-null  object 
 4   ACCIDENT_DATE  20814 non-null  object 
 5   INTERSECTION   20814 non-null  object 
 6   LOCATION       20814 non-null  object 
 7   CROSS_STREET   8289 non-null   object 
 8   CITY           20767 non-null  object 
 9   STATE          20811 non-null  object 
 10  POSTAL_CODE    20808 non-null  float64
 11  OFFENSE_CO     20814 non-null  int64  
 12  OFFENSE_DE     20814 non-null  object 
 13  LONGITUDE      20814 non-null  float64
 14  LATITUDE       20814 non-null  float64
 15  YEAR_          20814 non-null  int64  
 16  MONTH_         20814 non-null  int64  
 17  DOW_           20814 non-null  int64  
 18  MONTHF

In [184]:


df['CITY'].fillna(df['CITY'].mode()[0], inplace=True)
df['STATE'].fillna(df['STATE'].mode()[0], inplace=True)

df.isnull().sum()

/var/folders/l5/tf8z77h16qd31zzv9xhkk9g0cq9s3w/T/ipykernel_10126/1156505784.py:1: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df['CITY'].fillna(df['CITY'].mode()[0], inplace=True)
/var/folders/l5/tf8z77h16qd31zzv9xhkk9g0cq9s3w/T/ipykernel_10126/1156505784.py:2: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values

X                   64
Y                   64
OBJECTID             0
INCIDENTID           0
ACCIDENT_DATE        0
INTERSECTION         0
LOCATION             0
CROSS_STREET     12525
CITY                 0
STATE                0
POSTAL_CODE          6
OFFENSE_CO           0
OFFENSE_DE           0
LONGITUDE            0
LATITUDE             0
YEAR_                0
MONTH_               0
DOW_                 0
MONTHFULL            0
DOWFULL              0
QUARTER              0
dtype: int64

In [185]:
df[df['POSTAL_CODE'].isna()]

df.loc[(df['LOCATION'] == '1871 W SIM PARK DR') & (df['POSTAL_CODE'].isna()), 'POSTAL_CODE'] = 67203.0
df.loc[(df['LOCATION'] == '4217 W 9TH ST') & (df['POSTAL_CODE'].isna()), 'POSTAL_CODE'] = 67212.0

df[df['POSTAL_CODE'].isna()]


Empty DataFrame
Columns: [X, Y, OBJECTID, INCIDENTID, ACCIDENT_DATE, INTERSECTION, LOCATION, CROSS_STREET, CITY, STATE, POSTAL_CODE, OFFENSE_CO, OFFENSE_DE, LONGITUDE, LATITUDE, YEAR_, MONTH_, DOW_, MONTHFULL, DOWFULL, QUARTER]
Index: []

In [186]:
def get_random_hex_color():
    # Generate random RGB values
    r = random.randint(0, 255)
    g = random.randint(0, 255)
    b = random.randint(0, 255)
    # Convert to hex and format as #RRGGBB
    return "#{:02x}{:02x}{:02x}".format(r, g, b).upper()

In [187]:
#Return 10 most common values that appear in each
common_modes = df['LOCATION'].value_counts().index.intersection(df['CROSS_STREET'].value_counts().index)[:10]
print(common_modes)



Index(['E 21ST ST N', 'E 13TH ST N', 'E CENTRAL AVE', 'E HARRY ST',
       'E KELLOGG DR', 'E PAWNEE AVE', 'W 13TH ST N', 'W 21ST ST N',
       'W CENTRAL AVE', 'E LINCOLN ST'],
      dtype='object')


In [188]:
#Convert coordinates to radians to work with Haversine
#Haversine is used to calc distance between 2 points on a sphere ex:(Earth)
coords_rad = np.radians(df[['LATITUDE', 'LONGITUDE']].values)

coords_rad

array([[ 6.56330565e-01, -2.47831265e+00],
       [ 6.56066203e-01, -2.47801339e+00],
       [ 6.56064786e-01, -2.47801685e+00],
       ...,
       [ 6.57897958e-01, -1.69976720e+00],
       [-3.63028484e-08, -3.54301838e-07],
       [-3.63028484e-08, -3.54301838e-07]], shape=(20814, 2))

In [189]:
# Run DBSCAN clustering using the Haversine metric
# eps = 0.0002524 is about 1 mile
dbscan = DBSCAN(eps = 0.0000250 , min_samples=4, metric="haversine").fit(coords_rad)

#Assign the cluster labels to the DataFrame
df["CLUSTER"] = dbscan.labels_

df['CLUSTER'].tail(40)


#Intersections that are close will have the same number

20774    456
20775     93
20776     93
20777     93
20778     93
20779     93
20780     93
20781    125
20782     93
20783    190
20784     93
20785     93
20786     93
20787     93
20788     87
20789     93
20790     93
20791     93
20792     93
20793     93
20794    456
20795     88
20796     93
20797     88
20798    456
20799    456
20800     93
20801     93
20802    456
20803     93
20804     93
20805     88
20806    189
20807     88
20808     93
20809    189
20810     93
20811    190
20812     93
20813     93
Name: CLUSTER, dtype: int64

In [190]:
# #Create Folium Map around center

# min_lat, max_lat = 37.5, 37.9  # Latitude bounds for Wichita
# min_lon, max_lon = -97.5, -97.0  # Longitude bounds for Wichita

# # Filter your DataFrame to only include points within this bounding box
# filter_df = df[(df['LATITUDE'] >= min_lat) & (df['LATITUDE'] <= max_lat) &
#                  (df['LONGITUDE'] >= min_lon) & (df['LONGITUDE'] <= max_lon)]

# map_center = [filter_df['LATITUDE'].mean(), filter_df['LONGITUDE'].mean()]
# map = folium.Map(location=map_center, zoom_start=10 )

# cmap = plt.cm.get_cmap('cubehelix', 500)


# #Plot points on map with different colors based on cluster 
# for index, row in filter_df.iterrows(): 
#     # Get a color for the cluster using the colormap
#     cluster_color = cmap(row['CLUSTER'] % 500)  # Make sure to normalize the cluster value
#     cluster_color_hex = mcolors.rgb2hex(cluster_color[:3])  # Convert to hex color


#     folium.CircleMarker(
#         location=[row['LATITUDE'], row['LONGITUDE']],
#         radius=5,
#         color=cluster_color_hex,
#         fill=True,
#         fill_color=cluster_color_hex,
#         fill_opacity=0.6
#     ).add_to(map)

# # Display map in Jupyter (if you're using Jupyter)
# #Create Folium Map around center

# map

In [203]:

k_means = KMeans(n_clusters=1500, random_state=0)
k_means.fit(coords_rad)
df['K_CLUSTERS'] = k_means.labels_
# df['CENTROIDS'] = k_means.cluster_centers_

min_lat, max_lat = 37.5, 37.9  # Latitude bounds for Wichita
min_lon, max_lon = -97.5, -97.0  # Longitude bounds for Wichita

# Filter your DataFrame to only include points within this bounding box
filter_df = df[(df['LATITUDE'] >= min_lat) & (df['LATITUDE'] <= max_lat) &
                 (df['LONGITUDE'] >= min_lon) & (df['LONGITUDE'] <= max_lon)]

map_center = [filter_df['LATITUDE'].mean(), filter_df['LONGITUDE'].mean()]
map = folium.Map(location=map_center, zoom_start=10 )


# Create a color mapping for each cluster
cluster_colors = {cluster: get_random_hex_color() for cluster in df['K_CLUSTERS'].unique()}

for index, row in filter_df.iterrows():
    cluster_color = cluster_colors[row['K_CLUSTERS']]
    folium.CircleMarker(
        location=[row['LATITUDE'], row['LONGITUDE']],
        radius=2,
        color=cluster_color,
        fill=True,
        fill_color=cluster_color,
        fill_opacity=0.6
    ).add_to(map)
# Display map in Jupyter (if you're using Jupyter)
#Create Folium Map around center

for centroid in k_means.cluster_centers_:
    folium.CircleMarker(
        location=[centroid[0], centroid[1]],
        radius=8,
        color='black',
        fill=True,
        fill_color='black',
        fill_opacity=1.0,
        weight=2
    ).add_to(map)

map

